In [1]:
import gym
import pytz
from datetime import datetime, timedelta
import numpy as np
from gym_mtsim import MtSimulator, OrderType

In [2]:
from typing import List, Tuple, Dict, Any, Optional, Union, Callable

import copy
from datetime import datetime
from pathos.multiprocessing import ProcessingPool as Pool

import numpy as np
from scipy.special import expit

import matplotlib.pyplot as plt
import matplotlib.cm as plt_cm
import matplotlib.colors as plt_colors
import plotly.graph_objects as go

import gym
from gym import spaces
from gym.utils import seeding

class MtEnv(gym.Env):

    metadata = {'render.modes': ['human', 'simple_figure', 'advanced_figure']}

    def __init__(
            self, original_simulator: MtSimulator, trading_symbols: List[str],
            window_size: int, time_points: Optional[List[datetime]]=None,
            hold_threshold: float=0.5, close_threshold: float=0.5,
            fee: Union[float, Callable[[str], float]]=0.0005,
            symbol_max_orders: int=1, multiprocessing_processes: Optional[int]=None
        ) -> None:

        # validations
        # assert is for debugging (true return nothing, false return as ______)
        assert len(original_simulator.symbols_data) > 0, "no data available"
        assert len(original_simulator.symbols_info) > 0, "no data available"
        assert len(trading_symbols) > 0, "no trading symbols provided"
        assert 0. <= hold_threshold <= 1., "'hold_threshold' must be in range [0., 1.]"

        if not original_simulator.hedge:
            symbol_max_orders = 1

        for symbol in trading_symbols:
            assert symbol in original_simulator.symbols_info, f"symbol '{symbol}' not found"
            currency_profit = original_simulator.symbols_info[symbol].currency_profit
            assert original_simulator._get_unit_symbol_info(currency_profit) is not None, \
                   f"unit symbol for '{currency_profit}' not found"

        if time_points is None:
            time_points = original_simulator.symbols_data[trading_symbols[0]].index.to_pydatetime().tolist()
        assert len(time_points) > window_size, "not enough time points provided"

        # attributes
        self.seed()
        self.original_simulator = original_simulator
        self.trading_symbols = trading_symbols
        # The number of time points (current and previous points) as the length of each observation's features.
        self.window_size = window_size
        # Time move (index)
        self.time_points = time_points
        self.hold_threshold = hold_threshold
        self.close_threshold = close_threshold
        self.fee = fee
        self.symbol_max_orders = symbol_max_orders
        # max number of process for parallel processing
        self.multiprocessing_pool = Pool(multiprocessing_processes) if multiprocessing_processes else None
        
        ######################### ADD self.indicator #########################
        self.indicator = self._get_indicator()
        self.prices = self._get_prices()
        self.signal_features = self._process_data()
        self.features_shape = (window_size, self.signal_features.shape[1])

        # spaces
        self.action_space = spaces.Box(
            low=-np.inf, high=np.inf,
            shape=(len(self.trading_symbols) * (self.symbol_max_orders + 2),)
        )  # symbol -> [close_order_i(logic), hold(logic), volume]

        self.observation_space = spaces.Dict({
            'balance': spaces.Box(low=0, high=np.inf, shape=(1,)),
            'equity': spaces.Box(low=0 , high=np.inf, shape=(1,)),
            'margin': spaces.Box(low=-np.inf, high=np.inf, shape=(1,)),
            'features': spaces.Box(low=0, high=np.inf, shape=self.features_shape),
            'orders': spaces.Box(
                low=-np.inf, high=np.inf,
                shape=(len(self.trading_symbols), self.symbol_max_orders, 3)
            )  # symbol, order_i -> [entry_price, volume, profit]
        })

        # episode
        self._start_tick = self.window_size - 1
        self._end_tick = len(self.time_points) - 1
        self._done: bool = NotImplemented
        self._current_tick: int = NotImplemented
        self.simulator: MtSimulator = NotImplemented
        self.history: List[Dict[str, Any]] = NotImplemented


    def seed(self, seed: Optional[int]=None) -> List[int]:
        self.np_random, seed = seeding.np_random(seed)
        return [seed]


    def reset(self) -> Dict[str, np.ndarray]:
        self._done = False
        self._current_tick = self._start_tick
        self.simulator = copy.deepcopy(self.original_simulator)
        self.simulator.current_time = self.time_points[self._current_tick]
        self.history = [self._create_info()]
        return self._get_observation()


    def step(self, action: np.ndarray) -> Tuple[Dict[str, np.ndarray], float, bool, Dict[str, Any]]:
        orders_info, closed_orders_info = self._apply_action(action)

        self._current_tick += 1
        if self._current_tick == self._end_tick:
            self._done = True

        dt = self.time_points[self._current_tick] - self.time_points[self._current_tick - 1]
        self.simulator.tick(dt)

        step_reward = self._calculate_reward()

        info = self._create_info(
            orders=orders_info, closed_orders=closed_orders_info, step_reward=step_reward
        )
        observation = self._get_observation()
        self.history.append(info)

        return observation, step_reward, self._done, info


    def _apply_action(self, action: np.ndarray) -> Tuple[Dict, Dict]:
        orders_info = {}
        closed_orders_info = {symbol: [] for symbol in self.trading_symbols}

        k = self.symbol_max_orders + 2

        for i, symbol in enumerate(self.trading_symbols):
            symbol_action = action[k*i:k*(i+1)]
            close_orders_logit = symbol_action[:-2]
            hold_logit = symbol_action[-2]
            volume = symbol_action[-1]

            # The expit function, also known as the logistic sigmoid function
            close_orders_probability = expit(close_orders_logit)
            hold_probability = expit(hold_logit)
            hold = bool(hold_probability > self.hold_threshold)
            modified_volume = self._get_modified_volume(symbol, volume)

            symbol_orders = self.simulator.symbol_orders(symbol)
            orders_to_close_index = np.where(
                close_orders_probability[:len(symbol_orders)] > self.close_threshold
            )[0]
            orders_to_close = np.array(symbol_orders)[orders_to_close_index]

            for j, order in enumerate(orders_to_close):
                self.simulator.close_order(order)
                closed_orders_info[symbol].append(dict(
                    order_id=order.id, symbol=order.symbol, order_type=order.type,
                    volume=order.volume, fee=order.fee,
                    margin=order.margin, profit=order.profit,
                    close_probability=close_orders_probability[orders_to_close_index][j],
                ))

            orders_capacity = self.symbol_max_orders - (len(symbol_orders) - len(orders_to_close))
            orders_info[symbol] = dict(
                order_id=None, symbol=symbol, hold_probability=hold_probability,
                hold=hold, volume=volume, capacity=orders_capacity, order_type=None,
                modified_volume=modified_volume, fee=float('nan'), margin=float('nan'),
                error='',
            )

            if self.simulator.hedge and orders_capacity == 0:
                orders_info[symbol].update(dict(
                    error="cannot add more orders"
                ))
            elif not hold:
                order_type = OrderType.Buy if volume > 0. else OrderType.Sell
                fee = self.fee if type(self.fee) is float else self.fee(symbol)

                try:
                    order = self.simulator.create_order(order_type, symbol, modified_volume, fee)
                    new_info = dict(
                        order_id=order.id, order_type=order_type,
                        fee=fee, margin=order.margin,
                    )
                except ValueError as e:
                    new_info = dict(error=str(e))

                orders_info[symbol].update(new_info)

        return orders_info, closed_orders_info

    # Change to lower case
    def _get_prices(self, keys: List[str]=['Close', 'Open']) -> Dict[str, np.ndarray]:
        prices = {}

        for symbol in self.trading_symbols:
            get_price_at = lambda time: \
                self.original_simulator.price_at(symbol, time)[keys]

            if self.multiprocessing_pool is None:
                p = list(map(get_price_at, self.time_points))
            else:
                p = self.multiprocessing_pool.map(get_price_at, self.time_points)

            prices[symbol] = np.array(p)

        return prices
    
        ######################### ADD self.indicator #########################
        # columns=['Time', 'Open', 'High', 'Low', 'Close', 'Volume', '_', '_']
        # lowercase: ["open", "high", "low", "close"]
        
    def _get_indicator(self, keys: List[str]=['open','close','low','high','Volume','EFI','ADX','ATR','STOCHRSI']) -> Dict[str, np.ndarray]:
        #['Open','High', 'Low', 'Volume','EFI','CFI','ADX','STOCHRSI','KAMA']
        indicator = {}

        for symbol in self.trading_symbols:
            get_price_at = lambda time: \
                self.original_simulator.price_at(symbol, time)[keys]

            if self.multiprocessing_pool is None:
                p = list(map(get_price_at, self.time_points))
            else:
                p = self.multiprocessing_pool.map(get_price_at, self.time_points)

            indicator[symbol] = np.array(p)

        return indicator
    
    


    def _process_data(self) -> np.ndarray:
        # Add own indicator
        
        #data = self.prices
        data = self.indicator
        signal_features = np.column_stack(list(data.values()))
        return signal_features


    def _get_observation(self) -> Dict[str, np.ndarray]:
        features = self.signal_features[(self._current_tick-self.window_size+1):(self._current_tick+1)]

        orders = np.zeros(self.observation_space['orders'].shape)
        for i, symbol in enumerate(self.trading_symbols):
            symbol_orders = self.simulator.symbol_orders(symbol)
            for j, order in enumerate(symbol_orders):
                orders[i, j] = [order.entry_price, order.volume, order.profit]

        observation = {
            'balance': np.array([self.simulator.balance]),
            'equity': np.array([self.simulator.equity]),
            'margin': np.array([self.simulator.margin]),
            'features': features,
            'orders': orders,
        }
        return observation


    def _calculate_reward(self) -> float:
        prev_equity = self.history[-1]['equity']
        current_equity = self.simulator.equity
        step_reward = current_equity - prev_equity
        return step_reward


    def _create_info(self, **kwargs: Any) -> Dict[str, Any]:
        info = {k: v for k, v in kwargs.items()}
        info['balance'] = self.simulator.balance
        info['equity'] = self.simulator.equity
        info['margin'] = self.simulator.margin
        info['free_margin'] = self.simulator.free_margin
        info['margin_level'] = self.simulator.margin_level
        return info


    def _get_modified_volume(self, symbol: str, volume: float) -> float:
        si = self.simulator.symbols_info[symbol]
        v = abs(volume)
        v = np.clip(v, si.volume_min, si.volume_max)
        v = round(v / si.volume_step) * si.volume_step
        return v


    def render(self, mode: str='human', **kwargs: Any) -> Any:
        if mode == 'simple_figure':
            return self._render_simple_figure(**kwargs)
        if mode == 'advanced_figure':
            return self._render_advanced_figure(**kwargs)
        return self.simulator.get_state(**kwargs)


    def _render_simple_figure(
        self, figsize: Tuple[float, float]=(14, 6), return_figure: bool=False
    ) -> Any:
        fig, ax = plt.subplots(figsize=figsize, facecolor='white')

        cmap_colors = np.array(plt_cm.tab10.colors)[[0, 1, 4, 5, 6, 8]]
        cmap = plt_colors.LinearSegmentedColormap.from_list('mtsim', cmap_colors)
        symbol_colors = cmap(np.linspace(0, 1, len(self.trading_symbols)))

        for j, symbol in enumerate(self.trading_symbols):
            close_price = self.prices[symbol][:, 0]
            symbol_color = symbol_colors[j]

            ax.plot(self.time_points, close_price, c=symbol_color, marker='.', label=symbol)

            buy_ticks = []
            buy_error_ticks = []
            sell_ticks = []
            sell_error_ticks = []
            close_ticks = []

            for i in range(1, len(self.history)):
                tick = self._start_tick + i - 1

                order = self.history[i]['orders'].get(symbol, {})
                if order and not order['hold']:
                    if order['order_type'] == OrderType.Buy:
                        if order['error']:
                            buy_error_ticks.append(tick)
                        else:
                            buy_ticks.append(tick)
                    else:
                        if order['error']:
                            sell_error_ticks.append(tick)
                        else:
                            sell_ticks.append(tick)

                closed_orders = self.history[i]['closed_orders'].get(symbol, [])
                if len(closed_orders) > 0:
                    close_ticks.append(tick)

            tp = np.array(self.time_points)
            ax.plot(tp[buy_ticks], close_price[buy_ticks], '^', color='green')
            ax.plot(tp[buy_error_ticks], close_price[buy_error_ticks], '^', color='gray')
            ax.plot(tp[sell_ticks], close_price[sell_ticks], 'v', color='red')
            ax.plot(tp[sell_error_ticks], close_price[sell_error_ticks], 'v', color='gray')
            ax.plot(tp[close_ticks], close_price[close_ticks], '|', color='black')

            ax.tick_params(axis='y', labelcolor=symbol_color)
            ax.yaxis.tick_left()
            if j < len(self.trading_symbols) - 1:
                ax = ax.twinx()

        fig.suptitle(
            f"Balance: {self.simulator.balance:.6f} {self.simulator.unit} ~ "
            f"Equity: {self.simulator.equity:.6f} ~ "
            f"Margin: {self.simulator.margin:.6f} ~ "
            f"Free Margin: {self.simulator.free_margin:.6f} ~ "
            f"Margin Level: {self.simulator.margin_level:.6f}"
        )
        fig.legend(loc='right')

        if return_figure:
            return fig

        plt.show()


    def _render_advanced_figure(
            self, figsize: Tuple[float, float]=(1400, 600), time_format: str="%Y-%m-%d %H:%m",
            return_figure: bool=False
        ) -> Any:

        fig = go.Figure()

        cmap_colors = np.array(plt_cm.tab10.colors)[[0, 1, 4, 5, 6, 8]]
        cmap = plt_colors.LinearSegmentedColormap.from_list('mtsim', cmap_colors)
        symbol_colors = cmap(np.linspace(0, 1, len(self.trading_symbols)))
        get_color_string = lambda color: "rgba(%s, %s, %s, %s)" % tuple(color)

        extra_info = [
            f"balance: {h['balance']:.6f} {self.simulator.unit}<br>"
            f"equity: {h['equity']:.6f}<br>"
            f"margin: {h['margin']:.6f}<br>"
            f"free margin: {h['free_margin']:.6f}<br>"
            f"margin level: {h['margin_level']:.6f}"
            for h in self.history
        ]
        extra_info = [extra_info[0]] * (self.window_size - 1) + extra_info

        for j, symbol in enumerate(self.trading_symbols):
            close_price = self.prices[symbol][:, 0]
            symbol_color = symbol_colors[j]

            fig.add_trace(
                go.Scatter(
                    x=self.time_points,
                    y=close_price,
                    mode='lines+markers',
                    line_color=get_color_string(symbol_color),
                    opacity=1.0,
                    hovertext=extra_info,
                    name=symbol,
                    yaxis=f'y{j+1}',
                    legendgroup=f'g{j+1}',
                ),
            )

            fig.update_layout(**{
                f'yaxis{j+1}': dict(
                    tickfont=dict(color=get_color_string(symbol_color * [1, 1, 1, 0.8])),
                    overlaying='y' if j > 0 else None,
                    # position=0.035*j
                ),
            })

            trade_ticks = []
            trade_markers = []
            trade_colors = []
            trade_sizes = []
            trade_extra_info = []
            trade_max_volume = max([
                h.get('orders', {}).get(symbol, {}).get('modified_volume') or 0
                for h in self.history
            ])
            close_ticks = []
            close_extra_info = []

            for i in range(1, len(self.history)):
                tick = self._start_tick + i - 1

                order = self.history[i]['orders'].get(symbol)
                if order and not order['hold']:
                    marker = None
                    color = None
                    size = 8 + 22 * (order['modified_volume'] / trade_max_volume)
                    info = (
                        f"order id: {order['order_id'] or ''}<br>"
                        f"hold probability: {order['hold_probability']:.4f}<br>"
                        f"hold: {order['hold']}<br>"
                        f"volume: {order['volume']:.6f}<br>"
                        f"modified volume: {order['modified_volume']:.4f}<br>"
                        f"fee: {order['fee']:.6f}<br>"
                        f"margin: {order['margin']:.6f}<br>"
                        f"error: {order['error']}"
                    )

                    if order['order_type'] == OrderType.Buy:
                        marker = 'triangle-up'
                        color = 'gray' if order['error'] else 'green'
                    else:
                        marker = 'triangle-down'
                        color = 'gray' if order['error'] else 'red'

                    trade_ticks.append(tick)
                    trade_markers.append(marker)
                    trade_colors.append(color)
                    trade_sizes.append(size)
                    trade_extra_info.append(info)

                closed_orders = self.history[i]['closed_orders'].get(symbol, [])
                if len(closed_orders) > 0:
                    info = []
                    for order in closed_orders:
                        info_i = (
                            f"order id: {order['order_id']}<br>"
                            f"order type: {order['order_type'].name}<br>"
                            f"close probability: {order['close_probability']:.4f}<br>"
                            f"margin: {order['margin']:.6f}<br>"
                            f"profit: {order['profit']:.6f}"
                        )
                        info.append(info_i)
                    info = '<br>---------------------------------<br>'.join(info)

                    close_ticks.append(tick)
                    close_extra_info.append(info)

            fig.add_trace(
                go.Scatter(
                    x=np.array(self.time_points)[trade_ticks],
                    y=close_price[trade_ticks],
                    mode='markers',
                    hovertext=trade_extra_info,
                    marker_symbol=trade_markers,
                    marker_color=trade_colors,
                    marker_size=trade_sizes,
                    name=symbol,
                    yaxis=f'y{j+1}',
                    showlegend=False,
                    legendgroup=f'g{j+1}',
                ),
            )

            fig.add_trace(
                go.Scatter(
                    x=np.array(self.time_points)[close_ticks],
                    y=close_price[close_ticks],
                    mode='markers',
                    hovertext=close_extra_info,
                    marker_symbol='line-ns',
                    marker_color='black',
                    marker_size=7,
                    marker_line_width=1.5,
                    name=symbol,
                    yaxis=f'y{j+1}',
                    showlegend=False,
                    legendgroup=f'g{j+1}',
                ),
            )

        title = (
            f"Balance: {self.simulator.balance:.6f} {self.simulator.unit} ~ "
            f"Equity: {self.simulator.equity:.6f} ~ "
            f"Margin: {self.simulator.margin:.6f} ~ "
            f"Free Margin: {self.simulator.free_margin:.6f} ~ "
            f"Margin Level: {self.simulator.margin_level:.6f}"
        )
        fig.update_layout(
            title=title,
            xaxis_tickformat=time_format,
            width=figsize[0],
            height=figsize[1],
        )

        if return_figure:
            return fig

        fig.show()


    def close(self) -> None:
        plt.close()

In [3]:
sim = MtSimulator(
    unit='USD',
    balance=10000.,
    leverage=100.,
    stop_out_level=0.2,
    hedge=True,
    symbols_filename='1D_train_final.pkl'
)

In [4]:
env = MtEnv(
    original_simulator=sim,
    #trading_symbols=['EURUSD', 'USDJPY','GBPUSD','GBPCAD','GBPJPY'],
    trading_symbols=['EURUSD'],
    window_size=15,
    # time_points=[desired time points ...],
    hold_threshold=0.5,
    close_threshold=0.5,
    fee=lambda symbol: {
        'EURUSD': max(0., np.random.normal(0.0002, 0.00003)),
        #'USDJPY': max(0., np.random.normal(0.02, 0.003)),
        #'GBPUSD': max(0., np.random.normal(0.0002, 0.00003)),
        #'GBPCAD': max(0., np.random.normal(0.0002, 0.00003)),
        #'GBPJPY': max(0., np.random.normal(0.02, 0.003)),
    }[symbol],
    symbol_max_orders=2,
    multiprocessing_processes=2
)

In [5]:
print("env information:")

for symbol in env.prices:
    print(f"> prices[{symbol}].shape:", env.prices[symbol].shape)

print("> signal_features.shape:", env.signal_features.shape)
print("> features_shape:", env.features_shape)

env information:
> prices[EURUSD].shape: (1037, 2)
> signal_features.shape: (1037, 9)
> features_shape: (15, 9)


In [6]:
print(env.prices['EURUSD'])

[[1.04519 1.051  ]
 [1.04044 1.04524]
 [1.04871 1.04044]
 ...
 [1.22482 1.2216 ]
 [1.22961 1.22471]
 [1.22155 1.22963]]


# A2C 1D 4in All-symbol

In [7]:
import os
from stable_baselines3 import A2C
from stable_baselines3 import PPO
# A2C, PPO

models_dir = "models/A2C_1D_norm_EU"
logdir = "logs"
#tensorboard --logdir D:\Study\IS\code\gym-mtsim-main\gym_mtsim\logs\

if not os.path.exists(models_dir):
    os.makedirs(models_dir)

if not os.path.exists(logdir):
    os.makedirs(logdir)


# env = gym.make('forex-hedge-v0')

env.reset()


model = A2C('MultiInputPolicy', env, verbose=1, tensorboard_log = logdir)

TIMESTEPS = 10000
for i in range(1,101):    
    model.learn(total_timesteps=TIMESTEPS, reset_num_timesteps=False, tb_log_name="A2C_1D_norm_EU")
    model.save(f"{models_dir}/{TIMESTEPS*i}")

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


C:\Users\DELL\miniconda3\envs\gym\lib\site-packages\tensorflow\python\framework\dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
C:\Users\DELL\miniconda3\envs\gym\lib\site-packages\tensorflow\python\framework\dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
C:\Users\DELL\miniconda3\envs\gym\lib\site-packages\tensorflow\python\framework\dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
C:\Users\DELL\miniconda3\envs\gym\lib\site-packages\tensorflow\python\framework

Logging to logs\A2C_1D_norm_EU_0
------------------------------------
| time/                 |          |
|    fps                | 171      |
|    iterations         | 100      |
|    time_elapsed       | 2        |
|    total_timesteps    | 500      |
| train/                |          |
|    entropy_loss       | -5.68    |
|    explained_variance | 0        |
|    learning_rate      | 0.0007   |
|    n_updates          | 99       |
|    policy_loss        | 1.17e+03 |
|    std                | 1        |
|    value_loss         | 1.41e+05 |
------------------------------------
-------------------------------------
| time/                 |           |
|    fps                | 263       |
|    iterations         | 200       |
|    time_elapsed       | 3         |
|    total_timesteps    | 1000      |
| train/                |           |
|    entropy_loss       | -5.68     |
|    explained_variance | -1.19e-07 |
|    learning_rate      | 0.0007    |
|    n_updates          | 199   

-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 1.02e+03  |
|    ep_rew_mean        | -4.16e+03 |
| time/                 |           |
|    fps                | 515       |
|    iterations         | 1400      |
|    time_elapsed       | 13        |
|    total_timesteps    | 7000      |
| train/                |           |
|    entropy_loss       | -5.72     |
|    explained_variance | -11.4     |
|    learning_rate      | 0.0007    |
|    n_updates          | 1399      |
|    policy_loss        | -0.0438   |
|    std                | 1.01      |
|    value_loss         | 6.39e-05  |
-------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 1.02e+03  |
|    ep_rew_mean        | -4.99e+03 |
| time/                 |           |
|    fps                | 521       |
|    iterations         | 1500      |
|    time_elapsed       | 14        |
|    total_t

------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 1.76e+03 |
| time/                 |          |
|    fps                | 602      |
|    iterations         | 700      |
|    time_elapsed       | 5        |
|    total_timesteps    | 13500    |
| train/                |          |
|    entropy_loss       | -5.66    |
|    explained_variance | 1.19e-07 |
|    learning_rate      | 0.0007   |
|    n_updates          | 2699     |
|    policy_loss        | 2.59e+03 |
|    std                | 0.996    |
|    value_loss         | 2.82e+05 |
------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 1.02e+03  |
|    ep_rew_mean        | 1.76e+03  |
| time/                 |           |
|    fps                | 602       |
|    iterations         | 800       |
|    time_elapsed       | 6         |
|    total_timesteps    | 1400

...

------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 722      |
|    iterations         | 300      |
|    time_elapsed       | 2        |
|    total_timesteps    | 971500   |
| train/                |          |
|    entropy_loss       | -5.6     |
|    explained_variance | nan      |
|    learning_rate      | 0.0007   |
|    n_updates          | 194299   |
|    policy_loss        | -0       |
|    std                | 0.984    |
|    value_loss         | 0        |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 721      |
|    iterations         | 400      |
|    time_elapsed       | 2        |
|    total_timesteps    | 972000   |
|

------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 720      |
|    iterations         | 1600     |
|    time_elapsed       | 11       |
|    total_timesteps    | 978000   |
| train/                |          |
|    entropy_loss       | -5.6     |
|    explained_variance | nan      |
|    learning_rate      | 0.0007   |
|    n_updates          | 195599   |
|    policy_loss        | -0       |
|    std                | 0.984    |
|    value_loss         | 0        |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 719      |
|    iterations         | 1700     |
|    time_elapsed       | 11       |
|    total_timesteps    | 978500   |
|

------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 716      |
|    iterations         | 900      |
|    time_elapsed       | 6        |
|    total_timesteps    | 984500   |
| train/                |          |
|    entropy_loss       | -5.6     |
|    explained_variance | nan      |
|    learning_rate      | 0.0007   |
|    n_updates          | 196899   |
|    policy_loss        | -0       |
|    std                | 0.984    |
|    value_loss         | 0        |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 716      |
|    iterations         | 1000     |
|    time_elapsed       | 6        |
|    total_timesteps    | 985000   |
|

------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 719      |
|    iterations         | 200      |
|    time_elapsed       | 1        |
|    total_timesteps    | 991000   |
| train/                |          |
|    entropy_loss       | -5.6     |
|    explained_variance | nan      |
|    learning_rate      | 0.0007   |
|    n_updates          | 198199   |
|    policy_loss        | -0       |
|    std                | 0.984    |
|    value_loss         | 0        |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 716      |
|    iterations         | 300      |
|    time_elapsed       | 2        |
|    total_timesteps    | 991500   |
|

------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 719      |
|    iterations         | 1500     |
|    time_elapsed       | 10       |
|    total_timesteps    | 997500   |
| train/                |          |
|    entropy_loss       | -5.6     |
|    explained_variance | nan      |
|    learning_rate      | 0.0007   |
|    n_updates          | 199499   |
|    policy_loss        | -0       |
|    std                | 0.984    |
|    value_loss         | 0        |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 719      |
|    iterations         | 1600     |
|    time_elapsed       | 11       |
|    total_timesteps    | 998000   |
|

# PPO 1D 4in All-symbol

In [8]:
import os
from stable_baselines3 import A2C
from stable_baselines3 import PPO
# A2C, PPO

models_dir = "models/PPO_1D_norm_EU"
logdir = "logs"
#tensorboard --logdir D:\Study\IS\code\gym-mtsim-main\gym_mtsim\logs\

if not os.path.exists(models_dir):
    os.makedirs(models_dir)

if not os.path.exists(logdir):
    os.makedirs(logdir)


# env = gym.make('forex-hedge-v0')

env.reset()


model = PPO('MultiInputPolicy', env, verbose=1, tensorboard_log = logdir)

TIMESTEPS = 10000
for i in range(1,101):    
    model.learn(total_timesteps=TIMESTEPS, reset_num_timesteps=False, tb_log_name="PPO_1D_norm_EU")
    model.save(f"{models_dir}/{TIMESTEPS*i}")

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Logging to logs\PPO_1D_norm_EU_0
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.02e+03 |
|    ep_rew_mean     | 497      |
| time/              |          |
|    fps             | 1038     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.02e+03    |
|    ep_rew_mean          | -1.99e+03   |
| time/                   |             |
|    fps                  | 808         |
|    iterations           | 2           |
|    time_elapsed         | 5           |
|    total_timesteps      | 4096        |
| train/                  |             |
|    approx_kl            | 0.008352705 |
|    clip_fraction        | 0.0883      |
|    clip_range           | 0

Logging to logs\PPO_1D_norm_EU_0
----------------------------------
| rollout/           |           |
|    ep_len_mean     | 1.02e+03  |
|    ep_rew_mean     | -4.73e+03 |
| time/              |           |
|    fps             | 1057      |
|    iterations      | 1         |
|    time_elapsed    | 1         |
|    total_timesteps | 22528     |
----------------------------------
------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.02e+03     |
|    ep_rew_mean          | -4.31e+03    |
| time/                   |              |
|    fps                  | 800          |
|    iterations           | 2            |
|    time_elapsed         | 5            |
|    total_timesteps      | 24576        |
| train/                  |              |
|    approx_kl            | 0.0042143594 |
|    clip_fraction        | 0.0202       |
|    clip_range           | 0.2          |
|    entropy_loss         | -5.63        |
|    explained_

Logging to logs\PPO_1D_norm_EU_0
----------------------------------
| rollout/           |           |
|    ep_len_mean     | 1.02e+03  |
|    ep_rew_mean     | -4.23e+03 |
| time/              |           |
|    fps             | 1136      |
|    iterations      | 1         |
|    time_elapsed    | 1         |
|    total_timesteps | 43008     |
----------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.02e+03    |
|    ep_rew_mean          | -4.48e+03   |
| time/                   |             |
|    fps                  | 869         |
|    iterations           | 2           |
|    time_elapsed         | 4           |
|    total_timesteps      | 45056       |
| train/                  |             |
|    approx_kl            | 0.003805472 |
|    clip_fraction        | 0.0264      |
|    clip_range           | 0.2         |
|    entropy_loss         | -5.62       |
|    explained_variance   | 0

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.02e+03 |
|    ep_rew_mean     | -4.4e+03 |
| time/              |          |
|    fps             | 1067     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 63488    |
---------------------------------
----------------------------------------
| rollout/                |            |
|    ep_len_mean          | 1.02e+03   |
|    ep_rew_mean          | -3.71e+03  |
| time/                   |            |
|    fps                  | 824        |
|    iterations           | 2          |
|    time_elapsed         | 4          |
|    total_timesteps      | 65536      |
| train/                  |            |
|    approx_kl            | 0.00512609 |
|    clip_fraction        | 0.0596     |
|    clip_range           | 0.2        |
|    entropy_loss         | -5.52      |
|    explained_variance   | 6.38e-06   |
|    learning_rate        | 0.0003     |
|   

----------------------------------
| rollout/           |           |
|    ep_len_mean     | 1.02e+03  |
|    ep_rew_mean     | -2.54e+03 |
| time/              |           |
|    fps             | 1106      |
|    iterations      | 1         |
|    time_elapsed    | 1         |
|    total_timesteps | 83968     |
----------------------------------
------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.02e+03     |
|    ep_rew_mean          | -2.21e+03    |
| time/                   |              |
|    fps                  | 843          |
|    iterations           | 2            |
|    time_elapsed         | 4            |
|    total_timesteps      | 86016        |
| train/                  |              |
|    approx_kl            | 0.0032719567 |
|    clip_fraction        | 0.0166       |
|    clip_range           | 0.2          |
|    entropy_loss         | -5.54        |
|    explained_variance   | 0.000183     |
|    

...

Logging to logs\PPO_1D_norm_EU_0
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.02e+03 |
|    ep_rew_mean     | 1.15e+04 |
| time/              |          |
|    fps             | 961      |
|    iterations      | 1        |
|    time_elapsed    | 2        |
|    total_timesteps | 923648   |
---------------------------------
------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.02e+03     |
|    ep_rew_mean          | 1.12e+04     |
| time/                   |              |
|    fps                  | 737          |
|    iterations           | 2            |
|    time_elapsed         | 5            |
|    total_timesteps      | 925696       |
| train/                  |              |
|    approx_kl            | 0.0017174246 |
|    clip_fraction        | 0.00415      |
|    clip_range           | 0.2          |
|    entropy_loss         | -5.09        |
|    explained_variance  

Logging to logs\PPO_1D_norm_EU_0
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.02e+03 |
|    ep_rew_mean     | 1.27e+04 |
| time/              |          |
|    fps             | 1112     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 944128   |
---------------------------------
------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.02e+03     |
|    ep_rew_mean          | 1.23e+04     |
| time/                   |              |
|    fps                  | 818          |
|    iterations           | 2            |
|    time_elapsed         | 5            |
|    total_timesteps      | 946176       |
| train/                  |              |
|    approx_kl            | 0.0027093396 |
|    clip_fraction        | 0.00679      |
|    clip_range           | 0.2          |
|    entropy_loss         | -5.13        |
|    explained_variance  

Logging to logs\PPO_1D_norm_EU_0
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.02e+03 |
|    ep_rew_mean     | 1.29e+04 |
| time/              |          |
|    fps             | 1011     |
|    iterations      | 1        |
|    time_elapsed    | 2        |
|    total_timesteps | 964608   |
---------------------------------
------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.02e+03     |
|    ep_rew_mean          | 1.25e+04     |
| time/                   |              |
|    fps                  | 779          |
|    iterations           | 2            |
|    time_elapsed         | 5            |
|    total_timesteps      | 966656       |
| train/                  |              |
|    approx_kl            | 0.0070913946 |
|    clip_fraction        | 0.071        |
|    clip_range           | 0.2          |
|    entropy_loss         | -5.08        |
|    explained_variance  

Logging to logs\PPO_1D_norm_EU_0
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.02e+03 |
|    ep_rew_mean     | 1.35e+04 |
| time/              |          |
|    fps             | 998      |
|    iterations      | 1        |
|    time_elapsed    | 2        |
|    total_timesteps | 985088   |
---------------------------------
-------------------------------------------
| rollout/                |               |
|    ep_len_mean          | 1.02e+03      |
|    ep_rew_mean          | 1.35e+04      |
| time/                   |               |
|    fps                  | 735           |
|    iterations           | 2             |
|    time_elapsed         | 5             |
|    total_timesteps      | 987136        |
| train/                  |               |
|    approx_kl            | 0.00020141015 |
|    clip_fraction        | 0.00103       |
|    clip_range           | 0.2           |
|    entropy_loss         | -5.03         |
|    explai

Logging to logs\PPO_1D_norm_EU_0
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.02e+03 |
|    ep_rew_mean     | 1.29e+04 |
| time/              |          |
|    fps             | 1144     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 1005568  |
---------------------------------
------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.02e+03     |
|    ep_rew_mean          | 1.32e+04     |
| time/                   |              |
|    fps                  | 793          |
|    iterations           | 2            |
|    time_elapsed         | 5            |
|    total_timesteps      | 1007616      |
| train/                  |              |
|    approx_kl            | 0.0014219135 |
|    clip_fraction        | 0.00708      |
|    clip_range           | 0.2          |
|    entropy_loss         | -5.03        |
|    explained_variance  

## Change indi

In [9]:
class MtEnv(gym.Env):

    metadata = {'render.modes': ['human', 'simple_figure', 'advanced_figure']}

    def __init__(
            self, original_simulator: MtSimulator, trading_symbols: List[str],
            window_size: int, time_points: Optional[List[datetime]]=None,
            hold_threshold: float=0.5, close_threshold: float=0.5,
            fee: Union[float, Callable[[str], float]]=0.0005,
            symbol_max_orders: int=1, multiprocessing_processes: Optional[int]=None
        ) -> None:

        # validations
        # assert is for debugging (true return nothing, false return as ______)
        assert len(original_simulator.symbols_data) > 0, "no data available"
        assert len(original_simulator.symbols_info) > 0, "no data available"
        assert len(trading_symbols) > 0, "no trading symbols provided"
        assert 0. <= hold_threshold <= 1., "'hold_threshold' must be in range [0., 1.]"

        if not original_simulator.hedge:
            symbol_max_orders = 1

        for symbol in trading_symbols:
            assert symbol in original_simulator.symbols_info, f"symbol '{symbol}' not found"
            currency_profit = original_simulator.symbols_info[symbol].currency_profit
            assert original_simulator._get_unit_symbol_info(currency_profit) is not None, \
                   f"unit symbol for '{currency_profit}' not found"

        if time_points is None:
            time_points = original_simulator.symbols_data[trading_symbols[0]].index.to_pydatetime().tolist()
        assert len(time_points) > window_size, "not enough time points provided"

        # attributes
        self.seed()
        self.original_simulator = original_simulator
        self.trading_symbols = trading_symbols
        # The number of time points (current and previous points) as the length of each observation's features.
        self.window_size = window_size
        # Time move (index)
        self.time_points = time_points
        self.hold_threshold = hold_threshold
        self.close_threshold = close_threshold
        self.fee = fee
        self.symbol_max_orders = symbol_max_orders
        # max number of process for parallel processing
        self.multiprocessing_pool = Pool(multiprocessing_processes) if multiprocessing_processes else None
        
        ######################### ADD self.indicator #########################
        self.indicator = self._get_indicator()
        self.prices = self._get_prices()
        self.signal_features = self._process_data()
        self.features_shape = (window_size, self.signal_features.shape[1])

        # spaces
        self.action_space = spaces.Box(
            low=-np.inf, high=np.inf,
            shape=(len(self.trading_symbols) * (self.symbol_max_orders + 2),)
        )  # symbol -> [close_order_i(logic), hold(logic), volume]

        self.observation_space = spaces.Dict({
            'balance': spaces.Box(low=0, high=np.inf, shape=(1,)),
            'equity': spaces.Box(low=0 , high=np.inf, shape=(1,)),
            'margin': spaces.Box(low=-np.inf, high=np.inf, shape=(1,)),
            'features': spaces.Box(low=0, high=np.inf, shape=self.features_shape),
            'orders': spaces.Box(
                low=-np.inf, high=np.inf,
                shape=(len(self.trading_symbols), self.symbol_max_orders, 3)
            )  # symbol, order_i -> [entry_price, volume, profit]
        })

        # episode
        self._start_tick = self.window_size - 1
        self._end_tick = len(self.time_points) - 1
        self._done: bool = NotImplemented
        self._current_tick: int = NotImplemented
        self.simulator: MtSimulator = NotImplemented
        self.history: List[Dict[str, Any]] = NotImplemented


    def seed(self, seed: Optional[int]=None) -> List[int]:
        self.np_random, seed = seeding.np_random(seed)
        return [seed]


    def reset(self) -> Dict[str, np.ndarray]:
        self._done = False
        self._current_tick = self._start_tick
        self.simulator = copy.deepcopy(self.original_simulator)
        self.simulator.current_time = self.time_points[self._current_tick]
        self.history = [self._create_info()]
        return self._get_observation()


    def step(self, action: np.ndarray) -> Tuple[Dict[str, np.ndarray], float, bool, Dict[str, Any]]:
        orders_info, closed_orders_info = self._apply_action(action)

        self._current_tick += 1
        if self._current_tick == self._end_tick:
            self._done = True

        dt = self.time_points[self._current_tick] - self.time_points[self._current_tick - 1]
        self.simulator.tick(dt)

        step_reward = self._calculate_reward()

        info = self._create_info(
            orders=orders_info, closed_orders=closed_orders_info, step_reward=step_reward
        )
        observation = self._get_observation()
        self.history.append(info)

        return observation, step_reward, self._done, info


    def _apply_action(self, action: np.ndarray) -> Tuple[Dict, Dict]:
        orders_info = {}
        closed_orders_info = {symbol: [] for symbol in self.trading_symbols}

        k = self.symbol_max_orders + 2

        for i, symbol in enumerate(self.trading_symbols):
            symbol_action = action[k*i:k*(i+1)]
            close_orders_logit = symbol_action[:-2]
            hold_logit = symbol_action[-2]
            volume = symbol_action[-1]

            # The expit function, also known as the logistic sigmoid function
            close_orders_probability = expit(close_orders_logit)
            hold_probability = expit(hold_logit)
            hold = bool(hold_probability > self.hold_threshold)
            modified_volume = self._get_modified_volume(symbol, volume)

            symbol_orders = self.simulator.symbol_orders(symbol)
            orders_to_close_index = np.where(
                close_orders_probability[:len(symbol_orders)] > self.close_threshold
            )[0]
            orders_to_close = np.array(symbol_orders)[orders_to_close_index]

            for j, order in enumerate(orders_to_close):
                self.simulator.close_order(order)
                closed_orders_info[symbol].append(dict(
                    order_id=order.id, symbol=order.symbol, order_type=order.type,
                    volume=order.volume, fee=order.fee,
                    margin=order.margin, profit=order.profit,
                    close_probability=close_orders_probability[orders_to_close_index][j],
                ))

            orders_capacity = self.symbol_max_orders - (len(symbol_orders) - len(orders_to_close))
            orders_info[symbol] = dict(
                order_id=None, symbol=symbol, hold_probability=hold_probability,
                hold=hold, volume=volume, capacity=orders_capacity, order_type=None,
                modified_volume=modified_volume, fee=float('nan'), margin=float('nan'),
                error='',
            )

            if self.simulator.hedge and orders_capacity == 0:
                orders_info[symbol].update(dict(
                    error="cannot add more orders"
                ))
            elif not hold:
                order_type = OrderType.Buy if volume > 0. else OrderType.Sell
                fee = self.fee if type(self.fee) is float else self.fee(symbol)

                try:
                    order = self.simulator.create_order(order_type, symbol, modified_volume, fee)
                    new_info = dict(
                        order_id=order.id, order_type=order_type,
                        fee=fee, margin=order.margin,
                    )
                except ValueError as e:
                    new_info = dict(error=str(e))

                orders_info[symbol].update(new_info)

        return orders_info, closed_orders_info

    # Change to lower case
    def _get_prices(self, keys: List[str]=['Close', 'Open']) -> Dict[str, np.ndarray]:
        prices = {}

        for symbol in self.trading_symbols:
            get_price_at = lambda time: \
                self.original_simulator.price_at(symbol, time)[keys]

            if self.multiprocessing_pool is None:
                p = list(map(get_price_at, self.time_points))
            else:
                p = self.multiprocessing_pool.map(get_price_at, self.time_points)

            prices[symbol] = np.array(p)

        return prices
    
        ######################### ADD self.indicator #########################
        # columns=['Time', 'Open', 'High', 'Low', 'Close', 'Volume', '_', '_']
        # lowercase: ["open", "high", "low", "close"]
        
    def _get_indicator(self, keys: List[str]=['Open','Close','High', 'Low']) -> Dict[str, np.ndarray]:
        #['Open','High', 'Low', 'Volume','EFI','CFI','ADX','STOCHRSI','KAMA']
        indicator = {}

        for symbol in self.trading_symbols:
            get_price_at = lambda time: \
                self.original_simulator.price_at(symbol, time)[keys]

            if self.multiprocessing_pool is None:
                p = list(map(get_price_at, self.time_points))
            else:
                p = self.multiprocessing_pool.map(get_price_at, self.time_points)

            indicator[symbol] = np.array(p)

        return indicator
    
    


    def _process_data(self) -> np.ndarray:
        # Add own indicator
        
        #data = self.prices
        data = self.indicator
        signal_features = np.column_stack(list(data.values()))
        return signal_features


    def _get_observation(self) -> Dict[str, np.ndarray]:
        features = self.signal_features[(self._current_tick-self.window_size+1):(self._current_tick+1)]

        orders = np.zeros(self.observation_space['orders'].shape)
        for i, symbol in enumerate(self.trading_symbols):
            symbol_orders = self.simulator.symbol_orders(symbol)
            for j, order in enumerate(symbol_orders):
                orders[i, j] = [order.entry_price, order.volume, order.profit]

        observation = {
            'balance': np.array([self.simulator.balance]),
            'equity': np.array([self.simulator.equity]),
            'margin': np.array([self.simulator.margin]),
            'features': features,
            'orders': orders,
        }
        return observation


    def _calculate_reward(self) -> float:
        prev_equity = self.history[-1]['equity']
        current_equity = self.simulator.equity
        step_reward = current_equity - prev_equity
        return step_reward


    def _create_info(self, **kwargs: Any) -> Dict[str, Any]:
        info = {k: v for k, v in kwargs.items()}
        info['balance'] = self.simulator.balance
        info['equity'] = self.simulator.equity
        info['margin'] = self.simulator.margin
        info['free_margin'] = self.simulator.free_margin
        info['margin_level'] = self.simulator.margin_level
        return info


    def _get_modified_volume(self, symbol: str, volume: float) -> float:
        si = self.simulator.symbols_info[symbol]
        v = abs(volume)
        v = np.clip(v, si.volume_min, si.volume_max)
        v = round(v / si.volume_step) * si.volume_step
        return v


    def render(self, mode: str='human', **kwargs: Any) -> Any:
        if mode == 'simple_figure':
            return self._render_simple_figure(**kwargs)
        if mode == 'advanced_figure':
            return self._render_advanced_figure(**kwargs)
        return self.simulator.get_state(**kwargs)


    def _render_simple_figure(
        self, figsize: Tuple[float, float]=(14, 6), return_figure: bool=False
    ) -> Any:
        fig, ax = plt.subplots(figsize=figsize, facecolor='white')

        cmap_colors = np.array(plt_cm.tab10.colors)[[0, 1, 4, 5, 6, 8]]
        cmap = plt_colors.LinearSegmentedColormap.from_list('mtsim', cmap_colors)
        symbol_colors = cmap(np.linspace(0, 1, len(self.trading_symbols)))

        for j, symbol in enumerate(self.trading_symbols):
            close_price = self.prices[symbol][:, 0]
            symbol_color = symbol_colors[j]

            ax.plot(self.time_points, close_price, c=symbol_color, marker='.', label=symbol)

            buy_ticks = []
            buy_error_ticks = []
            sell_ticks = []
            sell_error_ticks = []
            close_ticks = []

            for i in range(1, len(self.history)):
                tick = self._start_tick + i - 1

                order = self.history[i]['orders'].get(symbol, {})
                if order and not order['hold']:
                    if order['order_type'] == OrderType.Buy:
                        if order['error']:
                            buy_error_ticks.append(tick)
                        else:
                            buy_ticks.append(tick)
                    else:
                        if order['error']:
                            sell_error_ticks.append(tick)
                        else:
                            sell_ticks.append(tick)

                closed_orders = self.history[i]['closed_orders'].get(symbol, [])
                if len(closed_orders) > 0:
                    close_ticks.append(tick)

            tp = np.array(self.time_points)
            ax.plot(tp[buy_ticks], close_price[buy_ticks], '^', color='green')
            ax.plot(tp[buy_error_ticks], close_price[buy_error_ticks], '^', color='gray')
            ax.plot(tp[sell_ticks], close_price[sell_ticks], 'v', color='red')
            ax.plot(tp[sell_error_ticks], close_price[sell_error_ticks], 'v', color='gray')
            ax.plot(tp[close_ticks], close_price[close_ticks], '|', color='black')

            ax.tick_params(axis='y', labelcolor=symbol_color)
            ax.yaxis.tick_left()
            if j < len(self.trading_symbols) - 1:
                ax = ax.twinx()

        fig.suptitle(
            f"Balance: {self.simulator.balance:.6f} {self.simulator.unit} ~ "
            f"Equity: {self.simulator.equity:.6f} ~ "
            f"Margin: {self.simulator.margin:.6f} ~ "
            f"Free Margin: {self.simulator.free_margin:.6f} ~ "
            f"Margin Level: {self.simulator.margin_level:.6f}"
        )
        fig.legend(loc='right')

        if return_figure:
            return fig

        plt.show()


    def _render_advanced_figure(
            self, figsize: Tuple[float, float]=(1400, 600), time_format: str="%Y-%m-%d %H:%m",
            return_figure: bool=False
        ) -> Any:

        fig = go.Figure()

        cmap_colors = np.array(plt_cm.tab10.colors)[[0, 1, 4, 5, 6, 8]]
        cmap = plt_colors.LinearSegmentedColormap.from_list('mtsim', cmap_colors)
        symbol_colors = cmap(np.linspace(0, 1, len(self.trading_symbols)))
        get_color_string = lambda color: "rgba(%s, %s, %s, %s)" % tuple(color)

        extra_info = [
            f"balance: {h['balance']:.6f} {self.simulator.unit}<br>"
            f"equity: {h['equity']:.6f}<br>"
            f"margin: {h['margin']:.6f}<br>"
            f"free margin: {h['free_margin']:.6f}<br>"
            f"margin level: {h['margin_level']:.6f}"
            for h in self.history
        ]
        extra_info = [extra_info[0]] * (self.window_size - 1) + extra_info

        for j, symbol in enumerate(self.trading_symbols):
            close_price = self.prices[symbol][:, 0]
            symbol_color = symbol_colors[j]

            fig.add_trace(
                go.Scatter(
                    x=self.time_points,
                    y=close_price,
                    mode='lines+markers',
                    line_color=get_color_string(symbol_color),
                    opacity=1.0,
                    hovertext=extra_info,
                    name=symbol,
                    yaxis=f'y{j+1}',
                    legendgroup=f'g{j+1}',
                ),
            )

            fig.update_layout(**{
                f'yaxis{j+1}': dict(
                    tickfont=dict(color=get_color_string(symbol_color * [1, 1, 1, 0.8])),
                    overlaying='y' if j > 0 else None,
                    # position=0.035*j
                ),
            })

            trade_ticks = []
            trade_markers = []
            trade_colors = []
            trade_sizes = []
            trade_extra_info = []
            trade_max_volume = max([
                h.get('orders', {}).get(symbol, {}).get('modified_volume') or 0
                for h in self.history
            ])
            close_ticks = []
            close_extra_info = []

            for i in range(1, len(self.history)):
                tick = self._start_tick + i - 1

                order = self.history[i]['orders'].get(symbol)
                if order and not order['hold']:
                    marker = None
                    color = None
                    size = 8 + 22 * (order['modified_volume'] / trade_max_volume)
                    info = (
                        f"order id: {order['order_id'] or ''}<br>"
                        f"hold probability: {order['hold_probability']:.4f}<br>"
                        f"hold: {order['hold']}<br>"
                        f"volume: {order['volume']:.6f}<br>"
                        f"modified volume: {order['modified_volume']:.4f}<br>"
                        f"fee: {order['fee']:.6f}<br>"
                        f"margin: {order['margin']:.6f}<br>"
                        f"error: {order['error']}"
                    )

                    if order['order_type'] == OrderType.Buy:
                        marker = 'triangle-up'
                        color = 'gray' if order['error'] else 'green'
                    else:
                        marker = 'triangle-down'
                        color = 'gray' if order['error'] else 'red'

                    trade_ticks.append(tick)
                    trade_markers.append(marker)
                    trade_colors.append(color)
                    trade_sizes.append(size)
                    trade_extra_info.append(info)

                closed_orders = self.history[i]['closed_orders'].get(symbol, [])
                if len(closed_orders) > 0:
                    info = []
                    for order in closed_orders:
                        info_i = (
                            f"order id: {order['order_id']}<br>"
                            f"order type: {order['order_type'].name}<br>"
                            f"close probability: {order['close_probability']:.4f}<br>"
                            f"margin: {order['margin']:.6f}<br>"
                            f"profit: {order['profit']:.6f}"
                        )
                        info.append(info_i)
                    info = '<br>---------------------------------<br>'.join(info)

                    close_ticks.append(tick)
                    close_extra_info.append(info)

            fig.add_trace(
                go.Scatter(
                    x=np.array(self.time_points)[trade_ticks],
                    y=close_price[trade_ticks],
                    mode='markers',
                    hovertext=trade_extra_info,
                    marker_symbol=trade_markers,
                    marker_color=trade_colors,
                    marker_size=trade_sizes,
                    name=symbol,
                    yaxis=f'y{j+1}',
                    showlegend=False,
                    legendgroup=f'g{j+1}',
                ),
            )

            fig.add_trace(
                go.Scatter(
                    x=np.array(self.time_points)[close_ticks],
                    y=close_price[close_ticks],
                    mode='markers',
                    hovertext=close_extra_info,
                    marker_symbol='line-ns',
                    marker_color='black',
                    marker_size=7,
                    marker_line_width=1.5,
                    name=symbol,
                    yaxis=f'y{j+1}',
                    showlegend=False,
                    legendgroup=f'g{j+1}',
                ),
            )

        title = (
            f"Balance: {self.simulator.balance:.6f} {self.simulator.unit} ~ "
            f"Equity: {self.simulator.equity:.6f} ~ "
            f"Margin: {self.simulator.margin:.6f} ~ "
            f"Free Margin: {self.simulator.free_margin:.6f} ~ "
            f"Margin Level: {self.simulator.margin_level:.6f}"
        )
        fig.update_layout(
            title=title,
            xaxis_tickformat=time_format,
            width=figsize[0],
            height=figsize[1],
        )

        if return_figure:
            return fig

        fig.show()


    def close(self) -> None:
        plt.close()

# A2C 1D Allin All-symbol

In [10]:
import os
from stable_baselines3 import A2C
from stable_baselines3 import PPO
# A2C, PPO

models_dir = "models/A2C_1D_noIndi_EU"
logdir = "logs"
#tensorboard --logdir D:\Study\IS\code\gym-mtsim-main\gym_mtsim\logs\

if not os.path.exists(models_dir):
    os.makedirs(models_dir)

if not os.path.exists(logdir):
    os.makedirs(logdir)


# env = gym.make('forex-hedge-v0')

env.reset()


model = A2C('MultiInputPolicy', env, verbose=1, tensorboard_log = logdir)

TIMESTEPS = 10000
for i in range(1,101):    
    model.learn(total_timesteps=TIMESTEPS, reset_num_timesteps=False, tb_log_name="A2C_1D_noIndi_EU")
    model.save(f"{models_dir}/{TIMESTEPS*i}")

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Logging to logs\A2C_1D_noIndi_EU_0
------------------------------------
| time/                 |          |
|    fps                | 595      |
|    iterations         | 100      |
|    time_elapsed       | 0        |
|    total_timesteps    | 500      |
| train/                |          |
|    entropy_loss       | -5.71    |
|    explained_variance | 5.57e-05 |
|    learning_rate      | 0.0007   |
|    n_updates          | 99       |
|    policy_loss        | 1.55e+03 |
|    std                | 1.01     |
|    value_loss         | 2.01e+05 |
------------------------------------
-------------------------------------
| time/                 |           |
|    fps                | 615       |
|    iterations         | 200       |
|    time_elapsed       | 1         |
|    total_timesteps    | 1000      |
| train/                |           |
|    entropy_loss       | -5.71     |
|    explain

-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 1.02e+03  |
|    ep_rew_mean        | -7.64e+03 |
| time/                 |           |
|    fps                | 661       |
|    iterations         | 1400      |
|    time_elapsed       | 10        |
|    total_timesteps    | 7000      |
| train/                |           |
|    entropy_loss       | -5.61     |
|    explained_variance | -9.56     |
|    learning_rate      | 0.0007    |
|    n_updates          | 1399      |
|    policy_loss        | 0.00465   |
|    std                | 0.983     |
|    value_loss         | 8.46e-06  |
-------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 1.02e+03  |
|    ep_rew_mean        | -7.97e+03 |
| time/                 |           |
|    fps                | 659       |
|    iterations         | 1500      |
|    time_elapsed       | 11        |
|    total_t

-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 1.02e+03  |
|    ep_rew_mean        | -5.11e+03 |
| time/                 |           |
|    fps                | 731       |
|    iterations         | 600       |
|    time_elapsed       | 4         |
|    total_timesteps    | 13000     |
| train/                |           |
|    entropy_loss       | -5.63     |
|    explained_variance | -6.23     |
|    learning_rate      | 0.0007    |
|    n_updates          | 2599      |
|    policy_loss        | -2.45e-06 |
|    std                | 0.99      |
|    value_loss         | 3.03e-13  |
-------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 1.02e+03  |
|    ep_rew_mean        | -5.44e+03 |
| time/                 |           |
|    fps                | 737       |
|    iterations         | 700       |
|    time_elapsed       | 4         |
|    total_t

-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 1.02e+03  |
|    ep_rew_mean        | -4.02e+03 |
| time/                 |           |
|    fps                | 689       |
|    iterations         | 1800      |
|    time_elapsed       | 13        |
|    total_timesteps    | 19000     |
| train/                |           |
|    entropy_loss       | -5.68     |
|    explained_variance | -4.74     |
|    learning_rate      | 0.0007    |
|    n_updates          | 3799      |
|    policy_loss        | 0.0092    |
|    std                | 1         |
|    value_loss         | 3.84e-06  |
-------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 1.02e+03  |
|    ep_rew_mean        | -4.33e+03 |
| time/                 |           |
|    fps                | 690       |
|    iterations         | 1900      |
|    time_elapsed       | 13        |
|    total_t

-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 1.02e+03  |
|    ep_rew_mean        | -5.48e+03 |
| time/                 |           |
|    fps                | 584       |
|    iterations         | 1000      |
|    time_elapsed       | 8         |
|    total_timesteps    | 25000     |
| train/                |           |
|    entropy_loss       | -5.68     |
|    explained_variance | 0         |
|    learning_rate      | 0.0007    |
|    n_updates          | 4999      |
|    policy_loss        | 0.0289    |
|    std                | 1         |
|    value_loss         | 2.41e-05  |
-------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 1.02e+03  |
|    ep_rew_mean        | -5.48e+03 |
| time/                 |           |
|    fps                | 585       |
|    iterations         | 1100      |
|    time_elapsed       | 9         |
|    total_t

...

------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 681      |
|    iterations         | 300      |
|    time_elapsed       | 2        |
|    total_timesteps    | 971500   |
| train/                |          |
|    entropy_loss       | -5.76    |
|    explained_variance | nan      |
|    learning_rate      | 0.0007   |
|    n_updates          | 194299   |
|    policy_loss        | -0       |
|    std                | 1.02     |
|    value_loss         | 0        |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 686      |
|    iterations         | 400      |
|    time_elapsed       | 2        |
|    total_timesteps    | 972000   |
|

------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 678      |
|    iterations         | 1600     |
|    time_elapsed       | 11       |
|    total_timesteps    | 978000   |
| train/                |          |
|    entropy_loss       | -5.76    |
|    explained_variance | nan      |
|    learning_rate      | 0.0007   |
|    n_updates          | 195599   |
|    policy_loss        | -0       |
|    std                | 1.02     |
|    value_loss         | 0        |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 680      |
|    iterations         | 1700     |
|    time_elapsed       | 12       |
|    total_timesteps    | 978500   |
|

------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 616      |
|    iterations         | 900      |
|    time_elapsed       | 7        |
|    total_timesteps    | 984500   |
| train/                |          |
|    entropy_loss       | -5.76    |
|    explained_variance | nan      |
|    learning_rate      | 0.0007   |
|    n_updates          | 196899   |
|    policy_loss        | -0       |
|    std                | 1.02     |
|    value_loss         | 0        |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 619      |
|    iterations         | 1000     |
|    time_elapsed       | 8        |
|    total_timesteps    | 985000   |
|

------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 670      |
|    iterations         | 200      |
|    time_elapsed       | 1        |
|    total_timesteps    | 991000   |
| train/                |          |
|    entropy_loss       | -5.76    |
|    explained_variance | nan      |
|    learning_rate      | 0.0007   |
|    n_updates          | 198199   |
|    policy_loss        | -0       |
|    std                | 1.02     |
|    value_loss         | 0        |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 667      |
|    iterations         | 300      |
|    time_elapsed       | 2        |
|    total_timesteps    | 991500   |
|

------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 644      |
|    iterations         | 1500     |
|    time_elapsed       | 11       |
|    total_timesteps    | 997500   |
| train/                |          |
|    entropy_loss       | -5.76    |
|    explained_variance | nan      |
|    learning_rate      | 0.0007   |
|    n_updates          | 199499   |
|    policy_loss        | -0       |
|    std                | 1.02     |
|    value_loss         | 0        |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 1.02e+03 |
|    ep_rew_mean        | 0        |
| time/                 |          |
|    fps                | 647      |
|    iterations         | 1600     |
|    time_elapsed       | 12       |
|    total_timesteps    | 998000   |
|

# PPO 1D All All-symbol

In [11]:
import os
from stable_baselines3 import A2C
from stable_baselines3 import PPO
# A2C, PPO

models_dir = "models/PPO_1D_noIndi_EU"
logdir = "logs"
#tensorboard --logdir D:\Study\IS\code\gym-mtsim-main\gym_mtsim\logs\

if not os.path.exists(models_dir):
    os.makedirs(models_dir)

if not os.path.exists(logdir):
    os.makedirs(logdir)


# env = gym.make('forex-hedge-v0')

env.reset()


model = PPO('MultiInputPolicy', env, verbose=1, tensorboard_log = logdir)

TIMESTEPS = 10000
for i in range(1,101):    
    model.learn(total_timesteps=TIMESTEPS, reset_num_timesteps=False, tb_log_name="PPO_1D_noIndi_EU")
    model.save(f"{models_dir}/{TIMESTEPS*i}")

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Logging to logs\PPO_1D_noIndi_EU_0
----------------------------------
| rollout/           |           |
|    ep_len_mean     | 1.02e+03  |
|    ep_rew_mean     | -9.94e+03 |
| time/              |           |
|    fps             | 1071      |
|    iterations      | 1         |
|    time_elapsed    | 1         |
|    total_timesteps | 2048      |
----------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.02e+03    |
|    ep_rew_mean          | -6.57e+03   |
| time/                   |             |
|    fps                  | 808         |
|    iterations           | 2           |
|    time_elapsed         | 5           |
|    total_timesteps      | 4096        |
| train/                  |             |
|    approx_kl            | 0.008184774 |
|    clip_fraction        | 0.0833      |
|    clip_range  

Logging to logs\PPO_1D_noIndi_EU_0
----------------------------------
| rollout/           |           |
|    ep_len_mean     | 1.02e+03  |
|    ep_rew_mean     | -6.55e+03 |
| time/              |           |
|    fps             | 869       |
|    iterations      | 1         |
|    time_elapsed    | 2         |
|    total_timesteps | 22528     |
----------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.02e+03    |
|    ep_rew_mean          | -6.1e+03    |
| time/                   |             |
|    fps                  | 706         |
|    iterations           | 2           |
|    time_elapsed         | 5           |
|    total_timesteps      | 24576       |
| train/                  |             |
|    approx_kl            | 0.005039482 |
|    clip_fraction        | 0.0585      |
|    clip_range           | 0.2         |
|    entropy_loss         | -5.59       |
|    explained_variance   |

Logging to logs\PPO_1D_noIndi_EU_0
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.02e+03 |
|    ep_rew_mean     | -4.7e+03 |
| time/              |          |
|    fps             | 886      |
|    iterations      | 1        |
|    time_elapsed    | 2        |
|    total_timesteps | 43008    |
---------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.02e+03    |
|    ep_rew_mean          | -4.16e+03   |
| time/                   |             |
|    fps                  | 692         |
|    iterations           | 2           |
|    time_elapsed         | 5           |
|    total_timesteps      | 45056       |
| train/                  |             |
|    approx_kl            | 0.005053595 |
|    clip_fraction        | 0.0365      |
|    clip_range           | 0.2         |
|    entropy_loss         | -5.58       |
|    explained_variance   | 4.65e-05 

Logging to logs\PPO_1D_noIndi_EU_0
----------------------------------
| rollout/           |           |
|    ep_len_mean     | 1.02e+03  |
|    ep_rew_mean     | -3.22e+03 |
| time/              |           |
|    fps             | 1162      |
|    iterations      | 1         |
|    time_elapsed    | 1         |
|    total_timesteps | 63488     |
----------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.02e+03    |
|    ep_rew_mean          | -2.81e+03   |
| time/                   |             |
|    fps                  | 791         |
|    iterations           | 2           |
|    time_elapsed         | 5           |
|    total_timesteps      | 65536       |
| train/                  |             |
|    approx_kl            | 0.006692869 |
|    clip_fraction        | 0.0316      |
|    clip_range           | 0.2         |
|    entropy_loss         | -5.54       |
|    explained_variance   |

Logging to logs\PPO_1D_noIndi_EU_0
----------------------------------
| rollout/           |           |
|    ep_len_mean     | 1.02e+03  |
|    ep_rew_mean     | -2.94e+03 |
| time/              |           |
|    fps             | 1022      |
|    iterations      | 1         |
|    time_elapsed    | 2         |
|    total_timesteps | 83968     |
----------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.02e+03    |
|    ep_rew_mean          | -2.78e+03   |
| time/                   |             |
|    fps                  | 726         |
|    iterations           | 2           |
|    time_elapsed         | 5           |
|    total_timesteps      | 86016       |
| train/                  |             |
|    approx_kl            | 0.008596437 |
|    clip_fraction        | 0.0897      |
|    clip_range           | 0.2         |
|    entropy_loss         | -5.5        |
|    explained_variance   |

...

Logging to logs\PPO_1D_noIndi_EU_0
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.02e+03 |
|    ep_rew_mean     | 1.56e+03 |
| time/              |          |
|    fps             | 1140     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 923648   |
---------------------------------
------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.02e+03     |
|    ep_rew_mean          | 1.3e+03      |
| time/                   |              |
|    fps                  | 828          |
|    iterations           | 2            |
|    time_elapsed         | 4            |
|    total_timesteps      | 925696       |
| train/                  |              |
|    approx_kl            | 0.0023734528 |
|    clip_fraction        | 0.00161      |
|    clip_range           | 0.2          |
|    entropy_loss         | -5.08        |
|    explained_variance

Logging to logs\PPO_1D_noIndi_EU_0
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.02e+03 |
|    ep_rew_mean     | 393      |
| time/              |          |
|    fps             | 1171     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 944128   |
---------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.02e+03    |
|    ep_rew_mean          | 583         |
| time/                   |             |
|    fps                  | 866         |
|    iterations           | 2           |
|    time_elapsed         | 4           |
|    total_timesteps      | 946176      |
| train/                  |             |
|    approx_kl            | 0.017270233 |
|    clip_fraction        | 0.14        |
|    clip_range           | 0.2         |
|    entropy_loss         | -5.09       |
|    explained_variance   | 0.000413 

Logging to logs\PPO_1D_noIndi_EU_0
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.02e+03 |
|    ep_rew_mean     | 3.86e+03 |
| time/              |          |
|    fps             | 1260     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 964608   |
---------------------------------
------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.02e+03     |
|    ep_rew_mean          | 3.85e+03     |
| time/                   |              |
|    fps                  | 884          |
|    iterations           | 2            |
|    time_elapsed         | 4            |
|    total_timesteps      | 966656       |
| train/                  |              |
|    approx_kl            | 7.776296e-05 |
|    clip_fraction        | 0            |
|    clip_range           | 0.2          |
|    entropy_loss         | -5.11        |
|    explained_variance

Logging to logs\PPO_1D_noIndi_EU_0
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.02e+03 |
|    ep_rew_mean     | 5.43e+03 |
| time/              |          |
|    fps             | 1268     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 985088   |
---------------------------------
------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.02e+03     |
|    ep_rew_mean          | 5.29e+03     |
| time/                   |              |
|    fps                  | 893          |
|    iterations           | 2            |
|    time_elapsed         | 4            |
|    total_timesteps      | 987136       |
| train/                  |              |
|    approx_kl            | 0.0062525407 |
|    clip_fraction        | 0.0667       |
|    clip_range           | 0.2          |
|    entropy_loss         | -5.09        |
|    explained_variance

Logging to logs\PPO_1D_noIndi_EU_0
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.02e+03 |
|    ep_rew_mean     | 6.2e+03  |
| time/              |          |
|    fps             | 1229     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 1005568  |
---------------------------------
------------------------------------------
| rollout/                |              |
|    ep_len_mean          | 1.02e+03     |
|    ep_rew_mean          | 5.78e+03     |
| time/                   |              |
|    fps                  | 905          |
|    iterations           | 2            |
|    time_elapsed         | 4            |
|    total_timesteps      | 1007616      |
| train/                  |              |
|    approx_kl            | 0.0026120988 |
|    clip_fraction        | 0.00249      |
|    clip_range           | 0.2          |
|    entropy_loss         | -5.04        |
|    explained_variance

In [12]:
print("--DONE--")

--DONE--
